#  <center> Taller  de Aprendizaje Automático </center>
##  <center> Taller 4: Detección de Anomalías  </center>

# Introducción

En la siguiente actividad se trabajará en la detección de anomalías sobre redes de computadoras a partir de datos de tráfico. El objetivo será construir un modelo capaz de distinguir entre malas conexiones o ataques, y buenas conexiones, llamadas normales. Para esto se utilizará una parte del conjunto [KDD Cup'99](https://scikit-learn.org/stable/datasets/real_world.html#kddcup99-dataset) pensada para evaluar métodos de detección de anomalías. 

Para los problemas de detección de anomalías generalmente no se cuenta con datos etiquetados para entrenar un detector. Por su definición las anomalías son eventos raros y por lo tanto poco frecuentes, lo que dificulta el etiquetado. Es por esto que este tipo de tareas generalmente son no supervisadas.

El enfoque más habitual para implementar soluciones para este tipo de problemas, es crear un modelo base a partir de un conjunto de datos "normales", es decir de los cuales se tenga cierta certeza de que todos fueron adquiridos en una situación normal. Luego, en producción se detectarán como datos anómalos todos aquellos que no se ajusten a este modelo. Para saber el grado de ajuste de los datos se debe seleccionar un punto de operación, es decir, determinar cuándo un dato se considera anómalo. En un ejemplo real, el cliente primero debería proporcionar una cantidad considerable de datos que representen el comportamiento normal de su sistema. Luego que se tiene el mejor modelo posible de estos datos, junto con el cliente, que es el que conoce su sistema, se debe determinar el punto de operación a partir del compromiso entre detectar la mayor cantidad de anomalías y obtener la menor cantidad de falsas alarmas posibles.

Para hacer investigación en la detección de anomalías, existen conjuntos de datos como el que se trabajará en esta actividad que si tienen etiquetas. Generalmente estas se obtienen provocando fallas y/o ataques intencionales a un sistema que se encuentra funcionando de manera normal. En esta actividad se separará el conjunto de entrenamiento en dos partes. La primera con una gran proporción de datos etiquetados como normales, simulará ser el conjunto que el cliente nos proporciona para entrenar nuestro modelo. El otro conjunto tendrá datos etiquetados como normales y como anómalos, que se utilizará para definir el punto de operación. Asimismo, se tendrá un conjunto de test asociados a este problema para evaluar la puesta en producción del modelo. 

## Objetivos


*   Abordar un problema de detección de anomalías, y ver las diferencias con un problema de clasificación convencional.
*   Trabajar con algoritmos de aprendizaje no supervisado.
*   Crear detectores compatibles con los *pipelines* de *scikit-learn*.


# Formas de trabajo

### Opción 1: Trabajar localmente

# Descargar los datos en su máquina personal y trabajar en su propio ambiente de desarrollo.

`conda activate TAA-py311`              
`jupyter-notebook`    

Los paquetes faltantes se pueden instalar desde el notebook haciendo:     
` !pip install paquete_faltante` 

### Opción 2:  Trabajar en *Colab*. 

<table align="left">
  <td>
    <a target="_blank" href="https://colab.research.google.com/github/TAA-fing/TAA-2024/blob/main/talleres/taller4_anomalias.ipynb"><img src="https://www.tensorflow.org/images/colab_logo_32px.png" />Ejecutar en Google Colab</a>
  </td>
</table>

Se puede trabajar en Google Colab. Para ello es necesario contar con una cuenta de **google drive** y ejecutar un notebook almacenado en dicha cuenta. De lo contrario, no se conservarán los cambios realizados en la sesión. En caso de ya contar con una cuenta, se puede abrir el notebook y luego ir a `Archivo-->Guardar una copia en drive`. 

# Datos

### Parte 1 - Levantar los Datos

#### Conjunto de Entrenamiento

El conjunto de datos [KDD Cup'99](https://scikit-learn.org/stable/datasets/real_world.html#kddcup99-dataset) contiene un conjunto de datos de tráfico de red que incluye tráfico normal y malicioso. El conjunto de datos para entrenamiento contiene 100655 instancias donde cada una cuenta con 41 características entre las que se encuentran la duración de la conexión, los tipos de protocolo, los tipos de servicios, entre otros. Por más información sobre el contenido de las características haga clic [aquí](http://kdd.ics.uci.edu/databases/kddcup99/task.html). Además, se cuenta con la columna *'labels'* que indica si el dato es normal o, de no serlo, indica el tipo de anomalía.

#### Ejercicios:

 - Ejecute la siguientes celdas para levantar el conjunto de datos de entrenamiento. 
 - Observar la cantidad de muestras por tipo. 
 - Determinar la relación entre datos normales y anómalos.  

In [ ]:
import pandas as pd
import numpy as np
import time
from sklearn.datasets import fetch_kddcup99

#Se obtienen los datos en formato de diccionario
KDDSA = fetch_kddcup99(subset='SA', as_frame=True, random_state=42)

#A partir del diccionario se crea un Dataframe con los datos
df = pd.DataFrame(data=KDDSA.frame.values, columns=KDDSA.frame.columns)

#Se estandariza el formato de los datos en el Dataframe 
types = [float, str, str,str, float, float, str, float, float, float, float, str, float, float,float, float, float, float, float, float, str, str, 
         float, float, float, float,float, float, float, float,float, float, float, float, float, float, float,float, float, float, float, str]

columns = df.columns
for i in range(len(columns)):
    df[columns[i]] = df[columns[i]].astype(types[i])
    if types[i] == str:
        df[columns[i]]= df[columns[i]].str.replace("b'", "")
        df[columns[i]]= df[columns[i]].str.replace("'", "")

#Visualizo
df.head()

In [ ]:
# ..

#### Conjunto de Test

Este problema tiene disponible un conjunto de datos para Test, estos se pueden encontar [aquí](https://kdd.ics.uci.edu/databases/kddcup99/kddcup99.html). 

#### Ejercicios:

 - Descargar y levantar los datos de Test. 
 - Separar los datos de las etiquetas.

In [ ]:
!pip install wget

In [ ]:
#start
start = time.time()

#Importo wget 
import wget

#Descargo los datos de Test
wget.download('http://kdd.ics.uci.edu/databases/kddcup99/corrected.gz')

#end
end = time.time()
print(np.round(end - start,3), 'segundos')

In [ ]:
#Levanto los datos de Test
test_data = pd.read_csv('./corrected.gz', header=None)

test_data.columns = columns

#Se estandariza el formato de los datos en el Dataframe 
types = [float, str, str,str, float, float, str, float, float, float, float, str, float, float,float, float, float, float, float, float, str, str, 
         float, float, float, float,float, float, float, float,float, float, float, float, float, float, float,float, float, float, float, str]

for i in range(len(columns)):
    test_data[columns[i]] = test_data[columns[i]].astype(types[i])

test_data.head()

In [ ]:
# ..

### Parte 2 - Preparar Conjuntos

#### Ejercicios:

Manteniendo el orden de los datos de Entrenamiento:

 - Separar las primeras 90000 muestras para entrenamiento con sus respectivas etiquetas. Estos deberían estar etiquetados como *normales*.
 - Separar las restantes muestras y sus respectivas etiquetas para validación.  Este conjunto permitirá fijar el punto de operación del modelo.

In [ ]:
# ..

In [ ]:
#Verifico las anomalias presentes en cada conjunto
print('Tipo de datos en Entrenamiento:\n',np.unique(y_train))
print('Tipo de datos en Validacion:\n',np.unique(y_val))
print('Tipo de datos en Test:\n',np.unique(y_test))

El código anterior muestra la cantidad de clases presente en cada conjunto. Verifique que en el conjunto de Entrenamiento solo hay muestras normales. 

Es importante tener en cuenta que los datos de Test presentan una distribución de probabilidad diferente a la de los datos de entrenamiento y validación, de hecho, contienen tipos específicos de ataques. Este aspecto es crucial para hacer la tarea de detección de anomalías más realista.

Los ataques informáticos pueden ser clasificados en diferentes categorías, las cuales se definen en función de su objetivo y método de ejecución. Es usual, categorizar los ataques en cuatro tipos principales: 

* **DoS**: Tienen como objetivo abrumar un sistema o red con una gran cantidad de tráfico, lo que puede resultar en una disminución o pérdida total del servicio , e.g. syn flood;
* **R2L**: Buscan obtener acceso no autorizado a un sistema desde una máquina remota, e.g. adivinar la contraseña;
* **U2R**: Buscan obtener acceso no autorizado a privilegios de superusuario local o raíz., e.g., various ''buffer overflow'' attacks;
* **probing**: Consisten en la vigilancia y exploración de, por ejemplo, puertos y/o servicios en busca de vulnerabilidades que puedan ser explotadas posteriormente.

A continuación, se otorga un diccionario de correspondencia entre las anomalías y la categoría correspondiente.

In [ ]:
# Se define un diccionario con la correspondencia entre la anomalía y la categoría
attack_dict = {
    'normal.': 'normal',
    
    'back.': 'DoS',
    'land.': 'DoS',
    'neptune.': 'DoS',
    'pod.': 'DoS',
    'smurf.': 'DoS',
    'teardrop.': 'DoS',
    'mailbomb.': 'DoS',
    'apache2.': 'DoS',
    'processtable.': 'DoS',
    'udpstorm.': 'DoS',
    
    'ipsweep.': 'Probe',
    'nmap.': 'Probe',
    'portsweep.': 'Probe',
    'satan.': 'Probe',
    'mscan.': 'Probe',
    'saint.': 'Probe',

    'ftp_write.': 'R2L',
    'guess_passwd.': 'R2L',
    'imap.': 'R2L',
    'multihop.': 'R2L',
    'phf.': 'R2L',
    'spy.': 'R2L',
    'warezclient.': 'R2L',
    'warezmaster.': 'R2L',
    'sendmail.': 'R2L',
    'named.': 'R2L',
    'snmpgetattack.': 'R2L',
    'snmpguess.': 'R2L',
    'xlock.': 'R2L',
    'xsnoop.': 'R2L',
    'worm.': 'R2L',
    
    'buffer_overflow.': 'U2R',
    'loadmodule.': 'U2R',
    'perl.': 'U2R',
    'rootkit.': 'U2R',
    'httptunnel.': 'U2R',
    'ps.': 'U2R',    
    'sqlattack.': 'U2R',
    'xterm.': 'U2R'
}

Antes de finalizar se deberán cambiar las etiquetas de los datos en todos los conjuntos a 0 y 1. Siendo 0 la etiqueta de la clase normal y 1 la etiqueta de la clase anómala.

#### Objetivos:
 - Cambiar las etiquetas de los datos en todos los conjuntos a 0 y 1.
 
**Comentario**: Se sugiere en alguna variable distinta conservar los valores originales.

In [ ]:
# ...

### Parte 3 - Preprocesar y Visualizar los Datos

Una vez armados los conjuntos de datos, se espera que se realice una exploración y análisis de los mismos. Conforme a lo anterior, se espera que se implemente  un pipeline de preprocesamiento adecuado para los datos en cuestión. 

#### Ejercicios:

 - Analizar y visualizar los datos. 
 - Implementar un **pipeline** que realice los los preprocesamientos que considere necesarios. 

In [ ]:
# ..

# Detección de anomalías

Si bien *scikit-learn* proporciona algunas herramientas para la detección de anomalías, esta actividad se centra en la utilización de algoritmos no supervisados generalmente pensados para otras tareas como: reducción de la dimensionalidad, y/o *clustering*. Específicamente se trabajará con: PCA, *K-Means*, y *Gaussian Mixture Model* (GMM).

## PCA


El análisis de componentes principales (**PCA**) es una técnica de reducción de la dimensionalidad que permite representar los datos en un espacio de menor dimensión manteniendo la mayor cantidad posible de información. 

En la *Parte 1* se deberá seleccionar la cantidad de componentes principales que se utilizarán en el modelo. También, se sugiere utilizar esta técnica como una herramienta de visualización de datos.

Luego, en la *Parte 2* se implementa un detector de anomalías utilizando esta técnica.

### Parte 1


#### Ejercicios:

 - Aplicar PCA sobre los datos de entrenamiento y graficar como varía el porcentaje de la varianza total en función de la cantidad de componentes principales (CPs). Se sugiere ver la sección *Choosing the Right Number of Dimensions* del capítulo 8 del libro. 
 - Determinar la cantidad de CPs de manera de mantener el *99%* de la varianza de los datos.
 - Utilizando PCA visualice los datos en dos o tres dimensiones. ¿Logra identificar clusters? *Para esta parte puede resultar útil comparar según la proyeccion de datos Normales contra las proyecciones de los datos Anómalos según el tipo de ataque.*

In [ ]:
# ..

### Parte 2

La forma más directa de hacer detección de anomalías utilizando PCA, es mediante el error de reconstrucción. Para esto primero se calculan los componentes principales a partir de los datos de entrenamiento. Luego para cada dato a analizar se lo proyecta sobre estos componentes, y se calcula su reconstrucción. Debido a que los CPs fueron calculado sólo con datos normales, se espera que la reconstrucción de datos anómalos tengan mayores errores. Es por esto que a partir del error de reconstrucción se puede determinar si un dato es anómalo o no.

#### Objetivos:

*   Implementar un detector tal como se describe arriba, utilizando RMSE para calcular el error. El mismo se debe definir como una clase de manera que sea compatible con los *pipelines* de *scikit-learn*. En la siguiente celda se muestra un *template* para crear la clase ([aquí](https://scikit-learn.org/stable/developers/develop.html) se pueden ver otros ejemplos).

*   Crear un *pipeline* que incluya el preprocesamiento y el detector implementado.
*   Entrenar el modelo de manera que mantenga el *99%* de la varianza. 
*   Proponga un punto de operación teniendo en cuenta que se quiere evitar un exceso de falsas alarmas. Para ello se recomienda graficar el compromiso entre *precision* y *recall* para distintos valores de *threshold* que definen el punto de operación. Ver la sección *Precision/Recall Trade-off* del capítulo 3 del libro.
*   Graficar los *scores* de los datos utilizados en el punto anterior, diferenciando con colores los datos normales de los anómalos.
*    Evaluar el desempeño en el conjunto de Validación y Test. Puede resultar útil tener la tasa de aciertos por categoría de anomalía.

In [ ]:
# Importo las librerías necesarias
from sklearn.base import BaseEstimator, OutlierMixin
from sklearn.utils.validation import check_array, check_is_fitted
from sklearn.decomposition import PCA
from sklearn.metrics import mean_squared_error

# Defino la clase AD_PCA que hereda de BaseEstimator y OutlierMixin lo que permite que sea compatible con el pipeline.  
# Esta clase debe tener los métodos fit y score. 
class AD_PCA(BaseEstimator, OutlierMixin):
    def __init__(self, n_comp=None):
        '''
        
        Constructor de la clase.

        Parametros:
            n_comp: cantidad de componentes principales a utilizar
            
        '''
        
        self.n_comp = n_comp
    
    def fit(self, X, y=None):
        '''
        
        Se entrena el modelo.

        Parametros:
            X: matriz de datos
            y: etiquetas (no son necesarias)
        
        Retorna:
            self: el objeto
            
        '''

        self.X = X
        self.y = y 
        
        # Agregar código---

        
        #------------------
        
        return self
    
    def score(self, X, y=None):  
        '''
        
        Se calcula el error de reconstrucción de cada muestra. 
        

        Parametros:
            X: matriz de datos
            y: etiquetas (no son necesarias)

        Retorna:
            score: el RMSE de cada muestra reconstruida. 

        '''
        
        # Se verifica que los datos sean válidos
        X = check_array(X)
        
        # Se verifica que el modelo haya sido entrenado
        check_is_fitted(self, ['X', 'y'])

        # Agregar código---
        

        #------------------
        return score

In [ ]:
# ..

Se otorga una función que, dadas las predicciones, devuelve la tasa de acierto por tipo de anomalía.

In [ ]:
def aciertos_por_clase(y, y_pred ,y_g_truth):
    
    '''
    
    Parametros:
        y = Etiquetas del conjunto en Formato 0 o 1
        y_pred = Predicciones en el conjunto en Formato True o False
        y_g_truth = Etiquetas del conjunto en formato string indicando el tipo de anomalía. 
    
    Retorna:
        Devuelve un Dataframe con la tasa de aciertos por Clase.
        
    '''
        
    aciertos = ( (y_pred.flatten()*1) == y.flatten())
    type_of_anomaly = list(np.unique(y_g_truth))
    acc_class = []
    
    for i_an in range(len(type_of_anomaly)):
        mask_anomaly  = y_g_truth == type_of_anomaly[i_an] 
        total_tipo = np.count_nonzero(mask_anomaly)
        acc_class.append(np.count_nonzero(aciertos & mask_anomaly)/total_tipo)
        
    return pd.DataFrame([acc_class], columns=type_of_anomaly)

In [ ]:
# ..

## K-Means

A continuación se implementará un detector de anomalías utilizando el modelo K-Means.

En la *Parte 1*, se llevará a cabo la determinación del número óptimo de clusters necesarios para el problema. En la *Parte 2* se implementará un detector de anomalías.

Para facilitar la construcción del detector, se sugiere implementar un único pipeline que incluya tanto el preprocesamiento como el modelo. 

### Parte 1


#### Ejercicio:

 - Implementar una forma de hallar la cantidad de clusters de K-Means óptima . Se sugiere ver la sección *Finding the optimal number of clusters* del Capítulo 9. 
 
**Comentario**: Emplear alguno de los métodos sugeridos toma un tiempo no menor, se sugiere: (i) economizar las búsquedas, (ii) utilizar semillas, (iii) en cuánto tenga los resultados guardelos en formato *.npy*, *.txt* u otro que considere, para que luego pueda cargar en caso que desee rehacer una gráfica. Seguir esta práctica evita que tenga que volver a correr el experimento.  

In [ ]:
# ..

### Parte 2


Una vez seleccionada la cantidad óptima de clusters, se procederá a construir el detector de anomalías utilizando el modelo K-Means. Hay diferentes formas de usar este algoritmo, se sugiere  entrenar el modelo primero y luego calcular la distancia al cluster más cercano. Si esta distancia supera un umbral a definir entonces la muestra se clasificará como anómala.

#### Ejercicios:

- Implementar un detector de anomalías utilizando *K-Means*. Para ello cree una clase y un *pipeline* que lo implemente de forma análoga a lo realizado con el método de PCA.
-   Proponga un punto de operación teniendo en cuenta el compromiso entre *precision* y *recall* para distintos valores de *threshold* que definen el punto de operación. 
-   Graficar los *scores* de los datos utilizados en el punto anterior, diferenciando con colores los datos normales de los anómalos. 
- Evaluar el desempeño en el conjunto de Validación y Test.

In [ ]:
# Importo las bibliotecas necesarias
from sklearn.base import BaseEstimator, OutlierMixin
from sklearn.cluster import KMeans
from sklearn.utils.validation import check_array, check_is_fitted


# Defino la clase AD_Kmeans que hereda de BaseEstimator y OutlierMixin lo que permite que sea compatible con el pipeline.
# Esta clase debe tener los métodos fit y score.
class AD_Kmeans(BaseEstimator, OutlierMixin):
    def __init__(self, n_clusters=None):
        '''
        
            Constructor de la clase.

            Parametros:
                n_clusters: cantidad de clusters a utilizar
                
        '''

        self.K = n_clusters
    
    def fit(self, X, y=None):
        '''
            Se entrena el modelo.

            Parametros:
                X: matriz de datos
                y: etiquetas (no son necesarias)

            Retorna:
                self: el objeto
        '''

        self.X = X
        self.y = y 
        
        # Agregar código---

        
         #------------------
            
        return self
    
    def score(self, X, y=None):
        '''
        
            Se calcula la distancia mínima de cada muestra a los centroides de los clusters.

            Parámetros:
                X: matriz de datos
                y: etiquetas (no son necesarias)
            
            Retorna:
                d_min: la distancia mínima de cada muestra a los centroides de los clusters.
        
        '''

        # Se verifica que los datos sean válidos
        X = check_array(X)

        # Se verifica que el modelo haya sido entrenado
        check_is_fitted(self, ['X', 'y'])

        # Agregar código---


        #------------------
    
        return d_min

In [ ]:
# ..

## Gaussian Mixtures Models

Por último, se implementará un detector de anomalías utilizando el modelo mezcla de gaussianas (GMM).

En la *Parte 1*, se llevará a cabo la determinación del número óptimo de clusters necesarios para el problema. Una vez seleccionado el número adecuado de clusters, se procederá a la construcción del clasificador en la *Parte 2*.

Nuevamente, para facilitar la construcción del detector, se sugiere implementar un único pipeline que incluya tanto el preprocesamiento como el modelo.

### Parte 1


Siga el ejemplo de la sección *Anomaly Detection Using Gaussian Mixture* en el Capítulo 9 del libro, y determine la cantidad óptima de mezclas a utilizar por el modelo.


#### Ejercicio:

 - Proponer una forma de hallar la cantidad óptima de mezclas a utilizar.
 
 **Comentario**: Emplear alguno de los métodos sugeridos toma un tiempo no menor, se sugiere: (i) economizar las búsquedas, (ii) utilizar semillas, (iii) en cuánto tenga los resultados guardelos en formato *.npy*, *.txt* u otro que considere, para que luego pueda cargar en caso que desee rehacer una gráfica. Seguir esta práctica evita que tenga que volver a correr el experimento.  

In [ ]:
# ..


### Parte 2

Siguiendo también el el ejemplo de la sección *Anomaly Detection Using Gaussian Mixture* en el Capítulo 9 del libro, construya y entrene un clasificador de anomalías utilizando la cantidad de mezclas determinadas en la parte anterior. 

Una vez entrenado el modelo, se calcula la log-verosimilitud de cada muestra y se umbraliza para detectar anomalías. Si el valor de la log-verosimilitud es menor que un umbral determinado, se considera que la muestra es anómala.

El valor del umbral se fija a partir de determinar la proporción de muestras que se clasifican como anómalas. Por ejemplo, si se sabe de antemano que los ataques constituyen un porcentaje $\alpha$ de las muestras, se puede calcular el valor que define el percentil correspondiente a este $\alpha$% en la escala de log-verosimilitud para clasificar las muestras como anómalas.


#### Ejercicios:

*   Implementar un detector que calcule el valor de los *scores*, la log-verosimilitud en este caso. En la siguiente celda se proporciona un *template* para la implementación del detector.
*   Fijar un umbral en validación utilizando algún percentil similar a lo realizado en el Capítulo 9 del libro. Se obtendrán distintos puntos de funcionamiento en función del percentil elegido. Discutir sobre los resultados obtenidos.
*   Evaluar el desempeño en el conjunto de Validación y Test. 

In [ ]:
# Importo las bibliotecas necesarias
from sklearn.mixture import GaussianMixture
from sklearn.base import BaseEstimator, OutlierMixin
from sklearn.utils.validation import check_array, check_is_fitted

# Defino la clase AD_GMM que hereda de BaseEstimator y OutlierMixin lo que permite que sea compatible con el pipeline.
# Esta clase debe tener los métodos fit y score.
class AD_GMM(BaseEstimator, OutlierMixin):
    def __init__(self, n_comp=None):
        '''
        
            Constructor de la clase.

            Parametros:
                n_comp: cantidad de componentes principales a utilizar
                
        '''

        self.n_comp = n_comp
    
    def fit(self, X, y=None):
        '''
        
            Se entrena el modelo.

            Parametros:
                X: matriz de datos
                y: etiquetas (no son necesarias)

            Retorna:
                self: el objeto

        '''

        self.classes_ = [1, 0]
        self.X = X
        self.y = y 
        
        # Agregar código---
        
 
        
        #------------
        return self
    
    def score(self, X, y=None):
        '''
        
            Se calcula la log-verosimilitud de cada muestra.
            
            Parametros:
                X: matriz de datos
                y: etiquetas (no son necesarias)
            
            Retorna:
                score: el score de cada muestra.
                
        '''

        # Se verifica que los datos sean válidos
        X = check_array(X)

        # Se verifica que el modelo haya sido entrenado
        check_is_fitted(self, ['X', 'y'])

        # Agregar código---


        
        #------------------
        
        return score

In [ ]:
# ..

# Opcional

*   Aplicar a los datos del problema alguno de los detectores de *sikit-learn* como: One-Class SVM, Isolation Forest
*   Realizar ingeniería de características.
*   Combinar PCA con K-Means y/o GMM


In [ ]:
# ..